# Geo2SigMap Tutorial: Visualizing Measurement Data on a Map.

In this notebook, we demonstrate how to visulizaed the measurements data on map using `bokeh`.

## Prequistic:

- Make sure you have Bokeh installed. Check the [Bokeh document](https://docs.bokeh.org/en/latest/docs/user_guide/output/jupyter.html#ug-output-jupyter) for more info.

For reference:

- Install the `bokeh` if you are using the `Jupyter Noetbook`.
```console
pip install bokeh
```
- Install both the `bokeh` and `jupyter_bokeh` if you are using the `JupyterLab`.
```console
pip install bokeh jupyter_bokeh
```



In [1]:
import pandas as pd
import geopandas as gpd

from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, LinearColorMapper, HoverTool, WheelZoomTool, CheckboxGroup, CustomJS, Button, Div
from bokeh.io import output_notebook
from bokeh.models import ColorBar
from bokeh.layouts import column, row
from bokeh.models.tiles import WMTSTileSource
from bokeh.palettes import Viridis256


In [2]:
# Enable Bokeh output inside Jupyter Notebook
output_notebook()

Loading BokehJS ...

## Step 1: Load the Measurement Data

The dataset contains signal measurements with the following attributes:

- **Latitude & Longitude**: GPS coordinates of the measurement.
- **RSRP (Reference Signal Received Power)**: Indicates the received signal strength in dBm.
- **PCI (Physical Cell ID)**: Identifies the serving cell. **Masked as PCI A-F** for privacy reasons.  
  - For detailed information, please refer to our [paper](https://arxiv.org/pdf/2312.14303).
- **Device**: The measurement device used.  
  - For more details, refer to our [paper](https://arxiv.org/pdf/2312.14303).


In [3]:
# Load the CSV file containing measurement data
measurement_df = pd.read_csv("../data/measurements/Duke_CBRS.csv")

measurement_df

PCI   latitude  longitude   device  rsrp
0       C  36.004076 -78.939464  Samsung  -124
1       C  36.004083 -78.939426  Samsung  -121
2       C  36.004062 -78.939488  Samsung  -125
3       C  36.003936 -78.939655  Samsung  -127
4       C  36.004032 -78.939543  Samsung  -127
...    ..        ...        ...      ...   ...
46650   A  35.999280 -78.937950    Pixel  -125
46651   D  35.999280 -78.937950    Pixel  -113
46652   D  35.999280 -78.937950    Pixel  -114
46653   C  35.999280 -78.937950    Pixel  -118
46654   A  35.999280 -78.937950    Pixel  -118

[46655 rows x 5 columns]

## Step 2: Convert GPS Coordinates to Web Mercator

Bokeh's tile-based maps (like OpenStreetMap) use the **Web Mercator (EPSG:3857)** projection. We need to transform **GPS (EPSG:4326)** latitude/longitude coordinates to **Web Mercator (EPSG:3857)**.

In [4]:
# Step 1: Create a GeoDataFrame from latitude/longitude
# Use points_from_xy(longitude, latitude) to generate geometries
geometry = gpd.points_from_xy(measurement_df['longitude'], measurement_df['latitude'])
gdf = gpd.GeoDataFrame(measurement_df, geometry=geometry, crs="EPSG:4326")

# Step 2: Reproject to Web Mercator (EPSG:3857)
gdf_web_mercator = gdf.to_crs("EPSG:3857")

# Extract Web Mercator coordinates as seprate columns
gdf_web_mercator['x'] = gdf_web_mercator.geometry.x
gdf_web_mercator['y'] = gdf_web_mercator.geometry.y
gdf_web_mercator

PCI   latitude  longitude   device  rsrp  \
0       C  36.004076 -78.939464  Samsung  -124   
1       C  36.004083 -78.939426  Samsung  -121   
2       C  36.004062 -78.939488  Samsung  -125   
3       C  36.003936 -78.939655  Samsung  -127   
4       C  36.004032 -78.939543  Samsung  -127   
...    ..        ...        ...      ...   ...   
46650   A  35.999280 -78.937950    Pixel  -125   
46651   D  35.999280 -78.937950    Pixel  -113   
46652   D  35.999280 -78.937950    Pixel  -114   
46653   C  35.999280 -78.937950    Pixel  -118   
46654   A  35.999280 -78.937950    Pixel  -118   

                               geometry             x             y  
0      POINT (-8787500.976 4301182.192) -8.787501e+06  4.301182e+06  
1       POINT (-8787496.66 4301183.197) -8.787497e+06  4.301183e+06  
2      POINT (-8787503.624 4301180.271) -8.787504e+06  4.301180e+06  
3      POINT (-8787522.196 4301163.036) -8.787522e+06  4.301163e+06  
4      POINT (-8787509.767 4301176.123) -8.787510e+06  4.301176e+06  
...                                 ...           ...           ...  
46650  POINT (-8787332.398 4300522.302) -8.787332e+06  4.300522e+06  
46651  POINT (-8787332.398 4300522.302) -8.787332e+06  4.300522e+06  
46652  POINT (-8787332.398 4300522.302) -8.787332e+06  4.300522e+06  
46653  POINT (-8787332.398 4300522.302) -8.787332e+06  4.300522e+06  
46654  POINT (-8787332.398 4300522.302) -8.787332e+06  4.300522e+06  

[46655 rows x 8 columns]

## Step 3: Create an Interactive Bokeh Map


You can use the following controls:
* Scroll wheel: Zoom
* Mouse right: Move

In [5]:
p = figure(
    title="Geo2SigMap Measurements on Duke Campus",
    x_axis_type="mercator",
    y_axis_type="mercator",
    width=900,   # Set figure width
    height=500,  # Set figure height
    tools="pan,reset,save",
    x_range=(gdf_web_mercator['x'].min() - 500, gdf_web_mercator['x'].max() + 500),
    y_range=(gdf_web_mercator['y'].min() - 500, gdf_web_mercator['y'].max() + 500)
)

zoom_tool = WheelZoomTool(zoom_on_axis=False)
p.add_tools(zoom_tool)  # Add the zoom tool with restrictions
p.toolbar.active_scroll = zoom_tool  # Make this the default zoom tool

# Add OSM Base Map
osm_tile = WMTSTileSource(
    url='https://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png',
    attribution="© OpenStreetMap contributors"
)
p.add_tile(osm_tile)

# Create Color Mapper for RSRP
color_mapper = LinearColorMapper(
    palette=Viridis256,
    low=gdf_web_mercator['rsrp'].min(),
    high=gdf_web_mercator['rsrp'].max()
)
gdf_dict =gdf_web_mercator[['x', 'y', 'rsrp', 'latitude', 'longitude', 'PCI', 'device']].to_dict(orient="list")

source = ColumnDataSource(gdf_dict)
filtered_source = ColumnDataSource(data=gdf_dict)

points = p.scatter(
    x='x',
    y='y',
    size=5,
    source=filtered_source,
    fill_color={'field': 'rsrp', 'transform': color_mapper},
    line_color=None,
    fill_alpha=0.7
)

# Add Color Bar
color_bar = ColorBar(
    color_mapper=color_mapper,
    label_standoff=12,
    location=(0,0),
    title='RSRP (dBm)'
)
p.add_layout(color_bar, 'right')

# Add Hover Tool
hover = HoverTool(tooltips=[
    ("Lat/Lon", "@latitude, @longitude"),
    ("RSRP", "@rsrp dBm"),
    ("Device", "@device"),
    ("PCI", "@PCI")
])
p.add_tools(hover)

# Create unique options for both category columns
category_1_options = sorted(list(set(measurement_df['device'])))
category_2_options = sorted(list(set(measurement_df['PCI'])))

# Checkbox for filtering category_1
checkbox_group_1 = CheckboxGroup(labels=category_1_options, active=list(range(len(category_1_options))))  # Default: all active

# Checkbox for filtering category_2
checkbox_group_2 = CheckboxGroup(labels=category_2_options, active=list(range(len(category_2_options))))  # Default: all active

# "Select All / Unselect All" buttons for category_1
select_all_1 = Button(label="Select All", button_type="success")
unselect_all_1 = Button(label="Unselect All", button_type="danger")

# "Select All / Unselect All" buttons for category_2
select_all_2 = Button(label="Select All", button_type="success")
unselect_all_2 = Button(label="Unselect All", button_type="danger")

# Live count of displayed points
count_div = Div(text=f"<b>Current Points: {len(gdf_web_mercator['x'])}</b>", styles={"font-size": "16px", "color": "green"})

# JavaScript callback for filtering based on both checkboxes
callback = CustomJS(args=dict(
    source=source, 
    filtered_source=filtered_source, 
    checkbox_group_1=checkbox_group_1, 
    checkbox_group_2=checkbox_group_2,
    count_div=count_div
), code="""
    var data = source.data;
    var f_data = {x: [], y: [], rsrp: [], latitude:[], PCI:[], device:[] };
    
    var selected_cat1 = checkbox_group_1.active.map(i => checkbox_group_1.labels[i]);
    var selected_cat2 = checkbox_group_2.active.map(i => checkbox_group_2.labels[i]);

    for (var i = 0; i < data['x'].length; i++) {
        if (selected_cat1.includes(data['device'][i]) && selected_cat2.includes(data['PCI'][i])) {
         for (var key in data) {
             console.log("123");
         }
         console.log("123");
            f_data['x'].push(data['x'][i]);
            f_data['y'].push(data['y'][i]);
            f_data['rsrp'].push(data['rsrp'][i]);
            f_data['latitude'].push(data['latitude'][i]);
            f_data['PCI'].push(data['PCI'][i]);
            f_data['device'].push(data['device'][i]);
        }
    }

    filtered_source.data = f_data;
    count_div.text = "<b>Current Points: " + f_data['x'].length + "</b>";
""")

# Attach callback to both checkboxes
checkbox_group_1.js_on_change('active', callback)
checkbox_group_2.js_on_change('active', callback)

# JavaScript callback for "Select All / Unselect All" buttons (Category 1)
select_all_1_callback = CustomJS(args=dict(checkbox_group=checkbox_group_1, callback=callback), code="""
    checkbox_group.active = [...Array(checkbox_group.labels.length).keys()];
    callback.execute();
""")
unselect_all_1_callback = CustomJS(args=dict(checkbox_group=checkbox_group_1, callback=callback), code="""
    checkbox_group.active = [];
    callback.execute();
""")
select_all_1.js_on_click(select_all_1_callback)
unselect_all_1.js_on_click(unselect_all_1_callback)

# JavaScript callback for "Select All / Unselect All" buttons (Category 2)
select_all_2_callback = CustomJS(args=dict(checkbox_group=checkbox_group_2, callback=callback), code="""
    checkbox_group.active = [...Array(checkbox_group.labels.length).keys()];
    callback.execute();
""")
unselect_all_2_callback = CustomJS(args=dict(checkbox_group=checkbox_group_2, callback=callback), code="""
    checkbox_group.active = [];
    callback.execute();
""")
select_all_2.js_on_click(select_all_2_callback)
unselect_all_2.js_on_click(unselect_all_2_callback)

# Layout with filter checkboxes, buttons, and count display
layout = column(
    row(column(select_all_1, unselect_all_1, checkbox_group_1),
        column(select_all_2, unselect_all_2, checkbox_group_2),
        count_div),
   # Live counter below the plot
    p,
    
)

show(layout)